# Tail Risk Hedged Portfolio Analysis:

> Long Duration Versus Tail Risk Strategy (Long Implied Volatility & STIRS Long-Only Momentum)

> Comparison by implementing Risk-Parity and Risk-Budgeted (60/40 and 60/20/20) Portfolios between the S&P500 and the above two investment overlays/options

In [226]:
import numpy as np
import pandas as pd
import edhec_risk_kit as erk
import matplotlib.pyplot as plt
import yfinance as yf

import ipywidgets as widgets
from ipywidgets import interact, interact_manual

%matplotlib inline
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [367]:
#Import Data

df = pd.read_excel('dd.xlsx', header=0, index_col=0, parse_dates=True)
vix = yf.download('^VIX', progress=False)['Adj Close']
vix = pd.DataFrame(vix)
vix.columns = ['Volatility']
df = df.merge(vix['Volatility'], on='Date')
data = df.drop('VIX Futures', axis=1).dropna()
rets = data.pct_change().dropna()

## Basic Summary Stats: March 2000 - July 2020

In [368]:
#Basic Summary Stats - 2000 to 2020
erk.summary_stats(rets, 0, 252).sort_values(by='Sharpe Ratio', ascending=False).T

Tail Risk UST Long   S&P500 Volatility
Total Return               384.0%   373.3%  217.33%      7.53%
Annualized Return           8.37%    8.26%    6.09%      0.35%
Annualized Vol              8.29%   12.03%    20.2%    119.39%
Skewness                     0.39     -0.1    -0.19       2.06
Kurtosis                    21.08     7.93    13.59      20.43
Cornish-Fisher VaR (5%)     0.57%    1.16%    1.86%      4.45%
Historic CVaR (5%)          1.25%    1.68%    3.07%     13.13%
Sharpe Ratio                 1.01     0.69      0.3          0
Sortino Ratio                1.17     0.98     0.38       0.01
Max Drawdown              -13.13%   -18.4%  -55.25%     -88.7%

In [450]:
fig = px.line(((1+rets['2000':]).cumprod()-1).dropna())
fig.update_layout(title = 'Performance: March, 2000 - July, 2020',
                   xaxis_title='Date',
                   yaxis_title='Returns (%)', font=dict(family="Segoe UI, monospace", size=13, color="#7f7f7f"),
                   legend_title_text='Securities', plot_bgcolor = 'White', yaxis_tickformat = '%')
fig.update_traces(hovertemplate='Date: %{x} <br>Return: %{y:.2%}') 

In [449]:
period = 126
fig = px.line(data.pct_change(period).dropna())
fig.update_layout(title = 'Rolling Six Month Returns',
                   xaxis_title='Date',
                   yaxis_title='Returns (%)', font=dict(family="Segoe UI, monospace", size=13, color="#7f7f7f"),
                   legend_title_text='Securities', plot_bgcolor = 'White', yaxis_tickformat = '%')
fig.update_traces(hovertemplate='Date: %{x} <br>Return: %{y:.2%}') 

In [448]:
mrets = rets.resample("M").apply(lambda x: ((x + 1).cumprod() - 1).last("D"))
def scatter(sec):
    if sec=='Volatility':
        fig = px.scatter(mrets[[sec, 'S&P500']], x=sec, y='S&P500', 
                     hover_name=mrets.index.strftime("%b %Y"), trendline="lowess", color=sec, color_continuous_scale='rdylgn')
    else:
        fig = px.scatter(mrets[[sec, 'S&P500']], x=sec, y='S&P500', range_x=(-0.15,0.15), range_y=(-0.15,0.15), 
                     hover_name=mrets.index.strftime("%b %Y"), trendline="lowess", color=sec, color_continuous_scale='rdylgn')
    
    fig.update_layout(title = 'Monthly Returns Scatter Plot of S&P500 versus ' + sec,
                   font=dict(family="Segoe UI, monospace", size=13, color="#7f7f7f"),
                   plot_bgcolor = 'White', yaxis_tickformat = '.2%', xaxis_tickformat = '.2%')
    return fig.show()
    
interact(scatter, sec=widgets.Dropdown(options=('Tail Risk', 'UST Long', 'Volatility'), value='UST Long', description='Security: '));

interactive(children=(Dropdown(description='Security: ', index=1, options=('Tail Risk', 'UST Long', 'Volatilit…

## Portfolio Risk Parity & Risk Budgeted Weight Drifts:

In [393]:
#Generate RP Weights for the two portfolios

import pybt as bt
lb = 90
rebal = 21

rp_weights1 = bt.SAA.rp_weight_resample(data[['Tail Risk', 'S&P500', 'Volatility']], lb, rebal)
rp_weights2 = bt.SAA.rp_weight_resample(data[['UST Long', 'S&P500']], lb, rebal)

In [394]:
#Plot Weights Drift
import plotly.express as px

fig = px.area(rp_weights1)
fig.update_layout(title = 'Tail Risk Portfolio: Risk-Parity Allocations:2000-2020',
                   xaxis_title='Date',
                   yaxis_title='Allocation (%)', font=dict(family="Segoe UI, monospace", size=13, color="#7f7f7f"),
                   legend_title_text='Securities', plot_bgcolor = 'White', yaxis_tickformat = '%')
fig.update_traces(hovertemplate='Date: %{x} <br>Allocation: %{y:.2%}') 

In [395]:
fig = px.area(rp_weights2)
fig.update_layout(title = 'Bond Portfolio: Risk-Parity Allocations: 2000-2020',
                   xaxis_title='Date',
                   yaxis_title='Allocation (%)', font=dict(family="Segoe UI, monospace", size=13, color="#7f7f7f"),
                   legend_title_text='Securities', plot_bgcolor = 'White', yaxis_tickformat = '%')
fig.update_traces(hovertemplate='Date: %{x} <br>Allocation: %{y:.2%}') 

## Performance Comparison:

In [398]:
#Tail Risk  - Risk Parity Portfolio Daily

rp_weights1.index.name = 'Date'
rp_tr = rets[['S&P500', 'Tail Risk', 'Volatility']]
rp_tr.columns = ['S&P500-R', 'Tail Risk-R', 'Volatility-R']
rp_tr = rp_tr.join(rp_weights1, on='Date')
rp_tr = rp_tr.ffill().dropna()
rp_tr = pd.DataFrame((rp_tr['S&P500-R']*rp_tr['S&P500'] + rp_tr['Tail Risk-R'] * rp_tr['Tail Risk'] + rp_tr['Volatility-R'] * rp_tr['Volatility']), columns=['Tail Risk - RP Portfolio'])


#Long Duration - Risk Parity Portfolio Daily

rp_weights2.index.name = 'Date'
rp_bond = rets[['S&P500', 'UST Long']]
rp_bond.columns = ['S&P500-R', 'UST Long-R']
rp_bond = rp_bond.join(rp_weights2, on='Date')
rp_bond = rp_bond.ffill().dropna()
rp_bond = pd.DataFrame(rp_bond['S&P500-R']*rp_bond['S&P500'] + rp_bond['UST Long-R'] * rp_bond['UST Long'], columns=['Long Duration - RP Portfolio'])

In [399]:
perfs = rp_tr.merge(rp_bond, on='Date').merge(data['S&P500'].pct_change().dropna(), on='Date')

In [461]:
perfs1 = perfs.copy()
perfs1['Tail Risk - RP Portfolio'] = perfs1['Tail Risk - RP Portfolio']/0.75 

def volm_rets(voladj, start, end):
    if voladj=='Yes':
        return qs.plots.returns(perfs['Tail Risk - RP Portfolio'][start:end], benchmark = perfs['Long Duration - RP Portfolio'][start:end], match_volatility=True)
    else:
        fig = px.line((1+perfs1[start:end]).cumprod()-1, hover_name=perfs1.index.strftime("%d %b %Y"))
        fig.update_layout(title = 'Performance Comparison: 2000-2020 (NOT Volatility Adjusted)',
                   xaxis_title='Date',
                   yaxis_title='Return (%)', font=dict(family="Segoe UI, monospace", size=13, color="#7f7f7f"),
                   legend_title_text='Portfolios', plot_bgcolor = 'White', yaxis_tickformat = '%')
        #fig.update_traces(hovertemplate='Date: %{x} <br>Return: %{y:.2%}')
        return fig.show()
    
style = {'description_width': 'initial'} 
interact(volm_rets,
                   start = widgets.DatePicker(value=perfs.index[0],style=style, description = 'Start Date: '),
                   end = widgets.DatePicker(value=perfs.index[-1],style=style,  description = 'End Date: '),
                   voladj = widgets.Dropdown(options=('Yes', 'No'), value='Yes', style=style, description='Volatility Adjusted: '));

interactive(children=(Dropdown(description='Volatility Adjusted: ', options=('Yes', 'No'), style=DescriptionSt…

## 1-Year Rolling Correlation of Portfolios with S&P500

In [438]:
def roll_corr(period):
    fig = px.line(perfs.rolling(period).corr(perfs['S&P500']).dropna().drop('S&P500', axis=1))
    fig.update_layout(title = 'Rolling ' + str(period) + ' Day Correlation with S&P500',
                       xaxis_title='Date',
                       yaxis_title='Correlation (%)', font=dict(family="Segoe UI, monospace", size=13, color="#7f7f7f"),
                       legend_title_text='Portfolios', plot_bgcolor = 'White', yaxis_tickformat = '%',
                       xaxis=dict(
        rangeselector=dict(
            buttons=list([
                dict(count=1,
                     label="1m",
                     step="month",
                     stepmode="backward"),
                dict(count=6,
                     label="6m",
                     step="month",
                     stepmode="backward"),
                dict(count=1,
                     label="YTD",
                     step="year",
                     stepmode="todate"),
                dict(count=1,
                     label="1y",
                     step="year",
                     stepmode="backward"),
                dict(step="all")
            ])
        ),
        rangeslider=dict(
            visible=True
        ),
        type="date"
    )
)

    fig.update_traces(hovertemplate='Date: %{x} <br>Correlation: %{y:.2%}')
    
    return fig.show()

interact(roll_corr, period=widgets.IntSlider(252, 21, 252*3, 21, description = 'Lookback Period: ', style=style));

interactive(children=(IntSlider(value=252, description='Lookback Period: ', max=756, min=21, step=21, style=Sl…

## Performance Summary Statistics: March, 2000 to July, 2020

In [459]:
erk.summary_stats(perfs1, 0, 252).sort_values(by='Sortino Ratio', ascending=False).T

Tail Risk - RP Portfolio Long Duration - RP Portfolio  \
Total Return                             608.11%                      447.41%   
Annualized Return                         10.65%                         9.2%   
Annualized Vol                             8.23%                        8.25%   
Skewness                                    0.75                        -0.46   
Kurtosis                                   13.86                        12.12   
Cornish-Fisher VaR (5%)                    0.58%                        0.79%   
Historic CVaR (5%)                         1.14%                        1.16%   
Sharpe Ratio                                1.29                         1.12   
Sortino Ratio                               1.81                          1.5   
Max Drawdown                             -10.75%                      -17.36%   

                          S&P500  
Total Return             224.26%  
Annualized Return          6.32%  
Annualized Vol            20.14%  
Skewness                   -0.19  
Kurtosis                    13.8  
Cornish-Fisher VaR (5%)    1.84%  
Historic CVaR (5%)         3.07%  
Sharpe Ratio                0.31  
Sortino Ratio               0.39  
Max Drawdown             -55.25%

In [451]:
mprets = perfs.resample("M").apply(lambda x: ((x + 1).cumprod() - 1).last("D"))

def scatterm(sec):
    fig = px.scatter(mprets[[sec, 'S&P500']], y=sec, x='S&P500', range_x=(-0.15,0.15), range_y=(-0.15,0.15), 
                     hover_name=mprets.index.strftime("%b %Y"), trendline="ols", color=sec, color_continuous_scale='rdylgn')
    
    fig.update_layout(title = 'Monthly Returns Scatter Plot of S&P500 versus ' + sec,
                   font=dict(family="Segoe UI, monospace", size=13, color="#7f7f7f"),
                   plot_bgcolor = 'White', yaxis_tickformat = '.2%', xaxis_tickformat = '.2%')
    return fig.show()
    
interact(scatterm, sec=widgets.Dropdown(options=('Tail Risk - RP Portfolio', 'Long Duration - RP Portfolio'), value='Tail Risk - RP Portfolio', description='Portfolio: '));

interactive(children=(Dropdown(description='Portfolio: ', options=('Tail Risk - RP Portfolio', 'Long Duration …

In [440]:
import quantstats as qs

In [441]:
#qs.reports.html(perfs['Tail Risk - RP Portfolio'], perfs['Long Duration - RP Portfolio'], output='TR-Bond-RP-Comps.html', title='Tail Risk RP versus Long Duration RP Tearsheet')
#qs.reports.html(perfs['Tail Risk - RP Portfolio'], perfs['S&P500'], output='TR-S&P-Comps.html', title='Tail Risk RP versus S&P500 Tearsheet')
#qs.reports.html(perfs['Long Duration - RP Portfolio'], perfs['S&P500'], output='Bond-S&P-Comps.html', title='Long Duration versus S&P500 Tearsheet')